In [1]:
from __future__ import print_function, division

from keras.datasets import mnist,fashion_mnist
from keras.layers import Input, Dense, Reshape, Flatten, Dropout, multiply, concatenate, Conv2DTranspose
from keras.layers import BatchNormalization, Activation, Embedding, ZeroPadding2D, Lambda
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Sequential, Model
from keras.optimizers import Adam
from keras.utils import to_categorical
import keras.backend as K

import matplotlib.pyplot as plt
import os
import numpy as np

class INFOGAN():
    def __init__(self):
        self.img_rows = 28
        self.img_cols = 28
        self.channels = 1
        self.num_classes = 10
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.latent_dim = 72


        optimizer = Adam(0.0002, 0.5)
        losses = ['binary_crossentropy', self.mutual_info_loss]

        # Build and the discriminator and recognition network
        self.discriminator, self.auxilliary = self.build_disk_and_q_net()

        self.discriminator.compile(loss=['binary_crossentropy'],
            optimizer=optimizer,
            metrics=['accuracy'])

        # Build and compile the recognition network Q
        self.auxilliary.compile(loss=[self.mutual_info_loss],
            optimizer=optimizer,
            metrics=['accuracy'])

        # Build the generator
        self.generator = self.build_generator()

        # The generator takes noise and the target label as input
        # and generates the corresponding digit of that label
        gen_input = Input(shape=(self.latent_dim,))
        img = self.generator(gen_input)

        # For the combined model we will only train the generator
        self.discriminator.trainable = False

        # The discriminator takes generated image as input and determines validity
        valid = self.discriminator(img)
        # The recognition network produces the label
        target_label = self.auxilliary(img)

        # The combined model  (stacked generator and discriminator)
        self.combined = Model(gen_input, [valid, target_label])
        self.combined.compile(loss=losses,
            optimizer=optimizer)


    def build_generator(self):

        model = Sequential()

        model.add(Dense(128 * 7 * 7, activation="relu", input_dim=self.latent_dim))
        model.add(Reshape((7, 7, 128)))
        model.add(BatchNormalization(momentum=0.8))
        model.add(UpSampling2D())
        model.add(Conv2D(128, kernel_size=5, padding="same"))
        model.add(Activation("relu"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(UpSampling2D())
        model.add(Conv2D(64, kernel_size=5, padding="same"))
        model.add(Activation("relu"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Conv2D(self.channels, kernel_size=5, padding='same'))
        model.add(Activation("tanh"))

        gen_input = Input(shape=(self.latent_dim,))
        img = model(gen_input)

        model.summary()

        return Model(gen_input, img)


    def build_disk_and_q_net(self):

        img = Input(shape=self.img_shape)

        # Shared layers between discriminator and recognition network
        model = Sequential()
        model.add(Conv2D(64, kernel_size=5, strides=2, input_shape=self.img_shape, padding="same"))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(Conv2D(128, kernel_size=5, strides=2, padding="same"))
        model.add(ZeroPadding2D(padding=((0,1),(0,1))))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Conv2D(256, kernel_size=5, strides=2, padding="same"))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Conv2D(512, kernel_size=3, strides=2, padding="same"))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Flatten())

        img_embedding = model(img)

        # Discriminator
        validity = Dense(1, activation='sigmoid')(img_embedding)

        # Recognition
        q_net = Dense(128, activation='relu')(img_embedding)
        label = Dense(self.num_classes, activation='softmax')(q_net)

        # Return discriminator and recognition network
        return Model(img, validity), Model(img, label)


    def mutual_info_loss(self, c, c_given_x):
        """The mutual information metric we aim to minimize"""
        eps = 1e-8
        conditional_entropy = K.mean(- K.sum(K.log(c_given_x + eps) * c, axis=1))
        entropy = K.mean(- K.sum(K.log(c + eps) * c, axis=1))

        return conditional_entropy + entropy

    def sample_generator_input(self, batch_size):
        # Generator inputs
        sampled_noise = np.random.normal(0, 1, (batch_size, 62))
        sampled_labels = np.random.randint(0, self.num_classes, batch_size).reshape(-1, 1)
        sampled_labels = to_categorical(sampled_labels, num_classes=self.num_classes)

        return sampled_noise, sampled_labels

    def train(self, epochs, batch_size=128, sample_interval=50):

        # Load the dataset
        (X_train, y_train), (_, _) = fashion_mnist.load_data()

        # Rescale -1 to 1
        X_train = (X_train.astype(np.float32) - 127.5) / 127.5
        X_train = np.expand_dims(X_train, axis=3)
        y_train = y_train.reshape(-1, 1)

        # Adversarial ground truths
        valid = np.ones((batch_size, 1))
        fake = np.zeros((batch_size, 1))

        nb_batches = int(X_train.shape[0] / batch_size)
        global_step = 0

        for epoch in range(epochs):

            for index in range(nb_batches):
                global_step += 1
                imgs = X_train[index * batch_size:(index + 1) * batch_size]
                # Sample noise and categorical labels
                sampled_noise, sampled_labels = self.sample_generator_input(batch_size)
                gen_input = np.concatenate((sampled_noise, sampled_labels), axis=1)

                # Generate a half batch of new images
                gen_imgs = self.generator.predict(gen_input)

                # Train on real and generated data
                d_loss_real = self.discriminator.train_on_batch(imgs, valid)
                d_loss_fake = self.discriminator.train_on_batch(gen_imgs, fake)

                # Avg. loss
                d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)

                # ---------------------
                #  Train Generator and Q-network
                # ---------------------

                g_loss = self.combined.train_on_batch(gen_input, [valid, sampled_labels])

                # Plot the progress
                print("epoch:%d step:%d [D loss: %.2f, acc.: %.2f%%] [Q loss: %.2f] [G loss: %.2f]" % (
                    epoch,global_step, d_loss[0], 100 * d_loss[1], g_loss[1], g_loss[2]))

                # If at save interval => save generated image samples
                if global_step % sample_interval == 0:
                    self.sample_images(epoch, global_step)

    def sample_images(self, epoch, global_step):
        r, c = 10, 10

        fig, axs = plt.subplots(r, c)
        for i in range(c):
            sampled_noise, _ = self.sample_generator_input(c)
            label = to_categorical(np.full(fill_value=i, shape=(r, 1)), num_classes=self.num_classes)
            gen_input = np.concatenate((sampled_noise, label), axis=1)
            gen_imgs = self.generator.predict(gen_input)
            gen_imgs = 0.5 * gen_imgs + 0.5
            for j in range(r):
                axs[j, i].imshow(gen_imgs[j, :, :, 0], cmap='gray')
                axs[j, i].axis('off')
        if not os.path.isdir('images_infogan_fashion_mnist'):
            os.mkdir('images_infogan_fashion_mnist')
        fig.savefig("images_infogan_fashion_mnist/epoch_%d_step_%d.png" % (epoch, global_step))
        plt.close()

if __name__ == '__main__':
    infogan = INFOGAN()
    infogan.train(epochs=100, batch_size=64, sample_interval=200)
#-*-coding:utf-8-*-

Using TensorFlow backend.


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_4 (Dense)              (None, 6272)              457856    
_________________________________________________________________
reshape_1 (Reshape)          (None, 7, 7, 128)         0         
_________________________________________________________________
batch_normalization_4 (Batch (None, 7, 7, 128)         512       
_________________________________________________________________
up_sampling2d_1 (UpSampling2 (None, 14, 14, 128)       0         
_________________________________________________________________
conv2d_5 (Conv2D)            (None, 14, 14, 128)       409728    
_________________________________________________________________
activation_1 (Activation)    (None, 14, 14, 128)       0         
_________________________________________________________________
batch_normalization_5 (Batch (None, 14, 14, 128)       512       
__________

/home/imi432_006/anaconda3/envs/tf/lib/python3.5/site-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


epoch:0 step:1 [D loss: 1.74, acc.: 24.22%] [Q loss: 0.59] [G loss: 2.77]
epoch:0 step:2 [D loss: 0.94, acc.: 56.25%] [Q loss: 1.50] [G loss: 2.70]
epoch:0 step:3 [D loss: 0.91, acc.: 58.59%] [Q loss: 2.19] [G loss: 3.09]
epoch:0 step:4 [D loss: 0.62, acc.: 67.19%] [Q loss: 2.30] [G loss: 2.69]
epoch:0 step:5 [D loss: 0.57, acc.: 64.06%] [Q loss: 2.07] [G loss: 2.73]
epoch:0 step:6 [D loss: 0.79, acc.: 59.38%] [Q loss: 1.97] [G loss: 2.47]
epoch:0 step:7 [D loss: 0.79, acc.: 59.38%] [Q loss: 1.94] [G loss: 2.57]
epoch:0 step:8 [D loss: 0.69, acc.: 65.62%] [Q loss: 1.96] [G loss: 2.87]
epoch:0 step:9 [D loss: 0.75, acc.: 62.50%] [Q loss: 1.77] [G loss: 2.79]
epoch:0 step:10 [D loss: 0.80, acc.: 60.94%] [Q loss: 1.86] [G loss: 2.69]
epoch:0 step:11 [D loss: 0.57, acc.: 68.75%] [Q loss: 2.02] [G loss: 2.70]
epoch:0 step:12 [D loss: 0.63, acc.: 64.84%] [Q loss: 1.79] [G loss: 2.76]
epoch:0 step:13 [D loss: 0.65, acc.: 69.53%] [Q loss: 1.66] [G loss: 2.49]
epoch:0 step:14 [D loss: 0.70, acc

epoch:0 step:114 [D loss: 0.45, acc.: 71.88%] [Q loss: 1.82] [G loss: 0.36]
epoch:0 step:115 [D loss: 0.43, acc.: 76.56%] [Q loss: 1.98] [G loss: 0.17]
epoch:0 step:116 [D loss: 0.42, acc.: 79.69%] [Q loss: 1.88] [G loss: 0.33]
epoch:0 step:117 [D loss: 0.40, acc.: 76.56%] [Q loss: 1.97] [G loss: 0.37]
epoch:0 step:118 [D loss: 0.52, acc.: 70.31%] [Q loss: 1.89] [G loss: 0.42]
epoch:0 step:119 [D loss: 0.45, acc.: 77.34%] [Q loss: 1.92] [G loss: 0.56]
epoch:0 step:120 [D loss: 0.49, acc.: 74.22%] [Q loss: 1.83] [G loss: 0.34]
epoch:0 step:121 [D loss: 0.52, acc.: 72.66%] [Q loss: 1.96] [G loss: 0.38]
epoch:0 step:122 [D loss: 0.41, acc.: 76.56%] [Q loss: 1.96] [G loss: 0.27]
epoch:0 step:123 [D loss: 0.40, acc.: 79.69%] [Q loss: 1.84] [G loss: 0.28]
epoch:0 step:124 [D loss: 0.41, acc.: 76.56%] [Q loss: 1.87] [G loss: 0.35]
epoch:0 step:125 [D loss: 0.46, acc.: 73.44%] [Q loss: 1.83] [G loss: 0.20]
epoch:0 step:126 [D loss: 0.43, acc.: 74.22%] [Q loss: 1.65] [G loss: 0.39]
epoch:0 step

...

epoch:99 step:93193 [D loss: 0.80, acc.: 9.38%] [Q loss: 0.84] [G loss: 0.00]
epoch:99 step:93194 [D loss: 0.79, acc.: 17.97%] [Q loss: 0.80] [G loss: 0.00]
epoch:99 step:93195 [D loss: 0.79, acc.: 17.19%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93196 [D loss: 0.80, acc.: 13.28%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93197 [D loss: 0.79, acc.: 17.19%] [Q loss: 0.83] [G loss: 0.02]
epoch:99 step:93198 [D loss: 0.80, acc.: 15.62%] [Q loss: 0.84] [G loss: 0.00]
epoch:99 step:93199 [D loss: 0.79, acc.: 17.97%] [Q loss: 0.84] [G loss: 0.00]
epoch:99 step:93200 [D loss: 0.79, acc.: 11.72%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93201 [D loss: 0.80, acc.: 12.50%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93202 [D loss: 0.79, acc.: 20.31%] [Q loss: 0.82] [G loss: 0.10]
epoch:99 step:93203 [D loss: 0.79, acc.: 14.06%] [Q loss: 0.83] [G loss: 0.01]
epoch:99 step:93204 [D loss: 0.78, acc.: 14.84%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93205 [D loss: 0.80, acc.: 11.72%] [Q l

epoch:99 step:93298 [D loss: 0.80, acc.: 15.62%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93299 [D loss: 0.80, acc.: 14.84%] [Q loss: 0.84] [G loss: 0.00]
epoch:99 step:93300 [D loss: 0.79, acc.: 13.28%] [Q loss: 0.81] [G loss: 0.00]
epoch:99 step:93301 [D loss: 0.81, acc.: 14.84%] [Q loss: 0.81] [G loss: 0.02]
epoch:99 step:93302 [D loss: 0.79, acc.: 15.62%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93303 [D loss: 0.79, acc.: 16.41%] [Q loss: 0.82] [G loss: 0.01]
epoch:99 step:93304 [D loss: 0.81, acc.: 10.94%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93305 [D loss: 0.78, acc.: 19.53%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93306 [D loss: 0.80, acc.: 11.72%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93307 [D loss: 0.80, acc.: 17.97%] [Q loss: 0.82] [G loss: 0.03]
epoch:99 step:93308 [D loss: 0.79, acc.: 18.75%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93309 [D loss: 0.79, acc.: 16.41%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93310 [D loss: 0.80, acc.: 11.72%] [Q 

epoch:99 step:93405 [D loss: 0.80, acc.: 12.50%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93406 [D loss: 0.80, acc.: 16.41%] [Q loss: 0.85] [G loss: 0.02]
epoch:99 step:93407 [D loss: 0.80, acc.: 11.72%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93408 [D loss: 0.79, acc.: 19.53%] [Q loss: 0.85] [G loss: 0.00]
epoch:99 step:93409 [D loss: 0.81, acc.: 10.16%] [Q loss: 0.82] [G loss: 0.01]
epoch:99 step:93410 [D loss: 0.79, acc.: 20.31%] [Q loss: 0.84] [G loss: 0.00]
epoch:99 step:93411 [D loss: 0.80, acc.: 14.84%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93412 [D loss: 0.79, acc.: 14.84%] [Q loss: 0.81] [G loss: 0.01]
epoch:99 step:93413 [D loss: 0.79, acc.: 15.62%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93414 [D loss: 0.79, acc.: 14.84%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93415 [D loss: 0.80, acc.: 14.84%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93416 [D loss: 0.80, acc.: 14.84%] [Q loss: 0.83] [G loss: 0.08]
epoch:99 step:93417 [D loss: 0.79, acc.: 12.50%] [Q 

epoch:99 step:93509 [D loss: 0.80, acc.: 10.94%] [Q loss: 0.83] [G loss: 0.02]
epoch:99 step:93510 [D loss: 0.80, acc.: 12.50%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93511 [D loss: 0.79, acc.: 17.19%] [Q loss: 0.84] [G loss: 0.00]
epoch:99 step:93512 [D loss: 0.81, acc.: 10.94%] [Q loss: 0.83] [G loss: 0.09]
epoch:99 step:93513 [D loss: 0.81, acc.: 10.94%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93514 [D loss: 0.79, acc.: 16.41%] [Q loss: 0.84] [G loss: 0.00]
epoch:99 step:93515 [D loss: 0.79, acc.: 15.62%] [Q loss: 0.83] [G loss: 0.01]
epoch:99 step:93516 [D loss: 0.79, acc.: 9.38%] [Q loss: 0.81] [G loss: 0.00]
epoch:99 step:93517 [D loss: 0.79, acc.: 12.50%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93518 [D loss: 0.79, acc.: 14.06%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93519 [D loss: 0.80, acc.: 12.50%] [Q loss: 0.81] [G loss: 0.00]
epoch:99 step:93520 [D loss: 0.79, acc.: 14.06%] [Q loss: 0.82] [G loss: 0.04]
epoch:99 step:93521 [D loss: 0.80, acc.: 9.38%] [Q lo

epoch:99 step:93614 [D loss: 0.79, acc.: 16.41%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93615 [D loss: 0.80, acc.: 18.75%] [Q loss: 0.83] [G loss: 0.00]
epoch:99 step:93616 [D loss: 0.79, acc.: 15.62%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93617 [D loss: 0.80, acc.: 14.84%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93618 [D loss: 0.79, acc.: 16.41%] [Q loss: 0.84] [G loss: 0.00]
epoch:99 step:93619 [D loss: 0.79, acc.: 14.84%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93620 [D loss: 0.79, acc.: 14.84%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93621 [D loss: 0.79, acc.: 11.72%] [Q loss: 0.84] [G loss: 0.01]
epoch:99 step:93622 [D loss: 0.78, acc.: 17.19%] [Q loss: 0.82] [G loss: 0.00]
epoch:99 step:93623 [D loss: 0.80, acc.: 15.62%] [Q loss: 0.81] [G loss: 0.00]
epoch:99 step:93624 [D loss: 0.79, acc.: 18.75%] [Q loss: 0.84] [G loss: 0.00]
epoch:99 step:93625 [D loss: 0.79, acc.: 13.28%] [Q loss: 0.81] [G loss: 0.03]
epoch:99 step:93626 [D loss: 0.80, acc.: 13.28%] [Q 